In [1]:
import torch
import torch.nn as nn
from torch import optim
import polars as pl
import pandas as pd
import ta
import numpy as np
import torch
import math
import plotly.graph_objects as go
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from sklearn.preprocessing import StandardScaler

In [2]:
TEST_SIZE = 5000
input_window = 32
delta_window = 4
batch_size = 128 # batch size

In [3]:
class PositionalEncoding(nn.Module):

    def __init__(self, d_model, max_len=5000):
        super(PositionalEncoding, self).__init__()       
        pe = torch.zeros(max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() * (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0).transpose(0, 1)
        #pe.requires_grad = False
        self.register_buffer('pe', pe)

    def forward(self, x):
        return x + self.pe[:x.size(0), :]

In [4]:
class TransAm(nn.Module):
    def __init__(self,feature_size=64,num_layers=2,dropout=0.15):
        super(TransAm, self).__init__()
        self.model_type = 'Transformer'
        
        self.src_mask = None
        self.input_embedding  = nn.Linear(122,feature_size)
        self.pos_encoder = PositionalEncoding(feature_size)
        self.encoder_layer = nn.TransformerEncoderLayer(d_model=feature_size, nhead=8, dropout=dropout)
        self.transformer_encoder = nn.TransformerEncoder(self.encoder_layer, num_layers=num_layers)        
        self.decoder = nn.Linear(feature_size,1)
        self.init_weights()

    def init_weights(self):
        initrange = 0.1    
        self.decoder.bias.data.zero_()
        self.decoder.weight.data.uniform_(-initrange, initrange)

    def forward(self,src):
        if self.src_mask is None or self.src_mask.size(0) != len(src):
            device = src.device
            mask = self._generate_square_subsequent_mask(len(src)).to(device)
            self.src_mask = mask
        src = self.input_embedding(src)
        src = self.pos_encoder(src)
        output = self.transformer_encoder(src,self.src_mask)#, self.src_mask)
        output = self.decoder(output)
        return output

    def _generate_square_subsequent_mask(self, sz):
        mask = (torch.triu(torch.ones(sz, sz)) == 1).transpose(0, 1)
        mask = mask.float().masked_fill(mask == 0, float('-inf')).masked_fill(mask == 1, float(0.0))
        return mask

In [5]:
pl_df = pl.read_parquet("./ETHUSDT_FEATURES_DATASET_136_23032023.parquet")
X = pl_df.select(pl.exclude(["time"]))[:-4].to_pandas()

rsi_2 = ta.momentum.RSIIndicator(close = X.close, window = 2)
rsi_5 = ta.momentum.RSIIndicator(close = X.close, window = 5)
rsi_10 = ta.momentum.RSIIndicator(close = X.close, window = 10)
rsi_20 = ta.momentum.RSIIndicator(close = X.close, window = 20)
X["RSI_5"] = rsi_5.rsi()
X["RSI_10"] = rsi_10.rsi()
X["RSI_20"] = rsi_20.rsi()

X["MACD_2"] = ta.trend.macd(X.close, window_slow = 5, window_fast = 2)
X["MACD_5"] = ta.trend.macd(X.close, window_slow = 10, window_fast = 5)
X["MACD_10"] = ta.trend.macd(X.close, window_slow = 20, window_fast = 10)
X["MACD_15"] = ta.trend.macd(X.close, window_slow = 15, window_fast = 10)

X["ADI"] = ta.volume.AccDistIndexIndicator(high = X.high, low = X.low, close = X.close, volume=X.volume).acc_dist_index()

X["ADX_2"] = ta.trend.ADXIndicator(high = X.high, low = X.low, close = X.close, window=2).adx() 
X["ADX_4"] = ta.trend.ADXIndicator(high = X.high, low = X.low, close = X.close, window=4).adx() 
X["ADX_8"] = ta.trend.ADXIndicator(high = X.high, low = X.low, close = X.close, window=8).adx() 

X["FII_2"] = ta.volume.ForceIndexIndicator(close = X.close, volume=X.volume, window = 2).force_index() 
X["FII_4"] = ta.volume.ForceIndexIndicator(close = X.close, volume=X.volume, window = 4).force_index() 
X["FII_8"] = ta.volume.ForceIndexIndicator(close = X.close, volume=X.volume, window = 8).force_index() 

X["SR_2"] = ta.momentum.StochasticOscillator(high = X.high, low = X.low, close = X.close, window = 2).stoch()
X["SR_4"] = ta.momentum.StochasticOscillator(high = X.high, low = X.low, close = X.close, window = 4).stoch()
X["SR_8"] = ta.momentum.StochasticOscillator(high = X.high, low = X.low, close = X.close, window = 8).stoch()

X["roc_2"] = ta.momentum.ROCIndicator(X.close, 2).roc()
X["roc_4"] = ta.momentum.ROCIndicator(X.close, 4).roc()
X["roc_8"] = ta.momentum.ROCIndicator(X.close, 8).roc()
X["roc_12"] = ta.momentum.ROCIndicator(X.close, 12).roc()

X["roc_v_2"] = ta.momentum.ROCIndicator(X.volume, 2).roc()
X["roc_v_4"] = ta.momentum.ROCIndicator(X.volume, 4).roc()
X["roc_v_8"] = ta.momentum.ROCIndicator(X.volume, 8).roc()
X["roc_v_12"] = ta.momentum.ROCIndicator(X.volume, 12).roc()

X["roc_buy_volume_sum_5_10"] = X.buy_volume_sum_5 - X.buy_volume_sum_10
X["roc_buy_volume_sum_5_30"] = X.buy_volume_sum_5 - X.buy_volume_sum_30
X["roc_buy_volume_sum_10_30"] = X.buy_volume_sum_10 - X.buy_volume_sum_30
X["roc_buy_volume_sum_10_60"] = X.buy_volume_sum_10 - X.buy_volume_sum_60
X["roc_buy_volume_sum_30_60"] = X.buy_volume_sum_30 - X.buy_volume_sum_60

X["roc_sell_volume_sum_5_10"] = X.sell_volume_sum_5 - X.sell_volume_sum_10
X["roc_sell_volume_sum_5_30"] = X.sell_volume_sum_5 - X.sell_volume_sum_30
X["roc_sell_volume_sum_10_30"] = X.sell_volume_sum_10 - X.sell_volume_sum_30
X["roc_sell_volume_sum_10_60"] = X.sell_volume_sum_10 - X.sell_volume_sum_60
X["roc_sell_volume_sum_30_60"] = X.sell_volume_sum_30 - X.sell_volume_sum_60

X["roc_buy_volume_std_5_10"] = X.buy_volume_std_5 - X.buy_volume_std_10
X["roc_buy_volume_std_5_30"] = X.buy_volume_std_5 - X.buy_volume_std_30
X["roc_buy_volume_std_10_30"] = X.buy_volume_std_10 - X.buy_volume_std_30
X["roc_buy_volume_std_10_60"] = X.buy_volume_std_10 - X.buy_volume_std_60
X["roc_buy_volume_std_30_60"] = X.buy_volume_std_30 - X.buy_volume_std_60

X["roc_sell_volume_std_5_10"] = X.sell_volume_std_5 - X.sell_volume_std_10
X["roc_sell_volume_std_5_30"] = X.sell_volume_std_5 - X.sell_volume_std_30
X["roc_sell_volume_std_10_30"] = X.sell_volume_std_10 - X.sell_volume_std_30
X["roc_sell_volume_std_10_60"] = X.sell_volume_std_10 - X.sell_volume_std_60
X["roc_sell_volume_std_30_60"] = X.sell_volume_std_30 - X.sell_volume_std_60

data_y = pd.DataFrame()
#data_y['target'] = pl_df[1:-3,['close']].to_pandas()
data_y['target'] = ta.trend.SMAIndicator(pl_df.to_pandas().close, window = 4).sma_indicator()[3:-1].reset_index(drop=True)
y = pd.DataFrame()

X.replace([np.inf, -np.inf], np.nan, inplace=True)
X.replace(np.nan, 0.0, inplace=True)
X = X[20:].reset_index(drop=True)

print(X.shape)

col = X.pop('close')
X.insert(0, 'close', col)

data_x = X.values.tolist()
feature_scaler = StandardScaler()
feature_scaler.fit(data_x)
data_x = feature_scaler.transform(data_x)

dataset_x = []
dataset_y = []
backtest_close = []
for i in range(input_window, len(data_x)-delta_window):
    dataset_x.append(data_x[i-input_window: i])
    dataset_y.append(data_x[i-input_window + delta_window: i+delta_window])
    backtest_close.append(data_x[i-1])
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

X_test_df = dataset_x[-50000:-20000]
X_train_df = dataset_x[:-50000]

y_test_df = dataset_y[-50000:-20000]
backtest_close = backtest_close[-50000:-20000]
y_train_df = dataset_y[:-50000]
device

/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:785: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:785: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py:780: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/home/sevenineone/anaconda3/envs/ml/lib/python3.8/site-packages/ta/trend.py

(195796, 122)


device(type='cuda')

In [6]:
class TimeSeriesDataset(Dataset):
    def __init__(self, x, y):
        #x = np.expand_dims(x, 2)
        self.x = x.astype(np.float32)
        self.y = y.astype(np.float32)
        
    def __len__(self):
        return len(self.x)

    def __getitem__(self, idx):
        return (self.x[idx], self.y[idx])

dataset_train = TimeSeriesDataset(np.array(X_train_df), np.array(y_train_df))
dataset_val = TimeSeriesDataset(np.array(X_test_df), np.array(y_test_df))

print("Train data shape", dataset_train.x.shape, dataset_train.y.shape)
print("Validation data shape", dataset_val.x.shape, dataset_val.y.shape)

Train data shape (145760, 32, 122) (145760, 32, 122)
Validation data shape (30000, 32, 122) (30000, 32, 122)


In [7]:
train_dataloader = DataLoader(dataset_train, batch_size=batch_size, shuffle=True)
val_dataloader = DataLoader(dataset_val, batch_size=batch_size, shuffle=False)
test_dataloader = DataLoader(dataset_val, batch_size=1, shuffle=False)

In [ ]:
model = TransAm().to(device)
model

In [ ]:
def run_epoch(dataloader, is_training=False):
    epoch_loss = 0

    if is_training:
        print("training ep...")
        model.train()
    else:
        print("eval ep...")
        model.eval()

    for idx, (x, y) in enumerate(dataloader):
        if is_training:
            optimizer.zero_grad()

        batchsize = x.shape[0]

        x = x.to(device).permute(1, 0, 2)
        y = y.to(device).permute(1, 0, 2)
        
        out = model(x)
        loss = criterion(out, y[:, :, 0:1])

        if is_training:
            loss.backward()
            optimizer.step()

        epoch_loss += (loss.detach().item() / (batchsize*input_window))

    lr = scheduler.get_last_lr()[0]

    return epoch_loss/len(dataloader), lr

LR = 0.0005
STEP_SIZE = 20
EPOCHS = 50

criterion = nn.MSELoss(reduction="sum")
optimizer = optim.Adam(model.parameters(), lr=LR, betas=(0.9, 0.98), eps=1e-9)
scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=STEP_SIZE, gamma=0.1)

for epoch in range(EPOCHS):
    loss_train, lr_train = run_epoch(train_dataloader, is_training=True)
    loss_val, lr_val = run_epoch(val_dataloader)
    scheduler.step()
    
    print('Epoch[{}/{}] | loss train:{:.10f}, test:{:.10f} | lr:{:.8f}'
              .format(epoch+1, EPOCHS, loss_train, loss_val, lr_train))

In [ ]:
#torch.save(model, "PATH_TO_MODEL")

In [8]:
model = torch.load("PATH_TO_MODEL").to(device)

In [9]:
def predict(dataloader):
    model.eval()
    predictions = []
    targets = []
    price = []
    i = 0
    for idx, (x, y) in enumerate(dataloader):

        batchsize = x.shape[0]
        x = x.to(device)
        y = y.to(device)
        x = x.to(device).permute(1, 0, 2)
        y = y.to(device).permute(1, 0, 2)
        
        out = model(x)
        price.append(x[-1, 0, 0].item())
        targets.append([sum(y[-4:, 0, 0]).item()/4])
        predictions.append([sum(out[-4:, 0, :]).item()/4])

    return predictions, targets, price
pred, targ, price = predict(test_dataloader)
pred = [row+[0]*121 for row in pred]
targ = [row+[0]*121 for row in targ]
pred, targ = feature_scaler.inverse_transform(pred), feature_scaler.inverse_transform(targ)
#pred, targ = target_scaler.inverse_transform(pred), target_scaler.inverse_transform(targ)
pred, targ = [row[0] for row in pred], [row[0] for row in targ]

In [10]:
fig = go.Figure()
fig.add_trace(go.Scatter(
                         y=pd.DataFrame(targ, dtype=float)[0],
                         mode='lines',
                         name='target',
                         line=dict(color='blue', width = 2)
                         ))
fig.add_trace(go.Scatter(
                         y=pd.DataFrame(pred, dtype=float)[0],
                         mode='lines',
                         name='predicted',
                         line=dict(color='red', width = 2)
                         ))
fig.show()

In [11]:
from sklearn.metrics import mean_absolute_percentage_error, mean_absolute_error, median_absolute_error, mean_squared_error
print(f"MSE: {mean_squared_error(targ, pred):.6f}")
print(f"MAE: {mean_absolute_error(targ, pred):.6f}")
print(f"MedAE: {median_absolute_error(targ, pred):.6f}")
print(f"MAPE: {mean_absolute_percentage_error(targ, pred):.6f}")


MSE: 4.648946
MAE: 1.350951
MedAE: 0.879988
MAPE: 0.000823


In [12]:
close = feature_scaler.inverse_transform(backtest_close)
close = [i[0] for i in close]

In [13]:
price = feature_scaler.inverse_transform([[row]+[0]*121 for row in price])
price = [i[0] for i in price]

In [14]:
len(pred), len(close)

(30000, 30000)

In [21]:
from backtest import MLBackTrader


test = MLBackTrader()
test.open_threshold = 3
#test.maker_fee_multiplier = 0
#test.taker_fee_multiplier = 0
#test.spread_dummy = 0
test.load_predicted(pred)
test.load_target(close)

In [22]:
test.run()

|32|
|OPEND LONG POSITION | 1689.48
|CLOSE LONG POSITION | 1685.35 | profit: -2.5814
|33|
|OPEND LONG POSITION | 1685.35
|CLOSE LONG POSITION | 1688.69 | profit: 1.1541
|40|
|OPEND LONG POSITION | 1680.15
|CLOSE LONG POSITION | 1678.88 | profit: -1.1489
|161|
|OPEND LONG POSITION | 1680.34
|CLOSE LONG POSITION | 1682.48 | profit: 0.55568
|287|
|OPEND LONG POSITION | 1683.42
|CLOSE LONG POSITION | 1681.25 | profit: -1.5998
|288|
|OPEND LONG POSITION | 1681.25
|CLOSE LONG POSITION | 1684.12 | profit: 0.92034
|425|
|OPEND LONG POSITION | 1683.62
|CLOSE LONG POSITION | 1687.96 | profit: 1.6545
|430|
|OPEND LONG POSITION | 1685.58
|CLOSE LONG POSITION | 1684.59 | profit: -1.0106
|431|
|OPEND LONG POSITION | 1684.59
|CLOSE LONG POSITION | 1684.54 | profit: -0.54037
|439|
|OPEND LONG POSITION | 1679.18
|CLOSE LONG POSITION | 1678.03 | profit: -1.0886
|442|
|OPEND LONG POSITION | 1675.47
|CLOSE LONG POSITION | 1674.92 | profit: -0.78759
|488|
|OPEND LONG POSITION | 1671.12
|CLOSE LONG POSITION

In [23]:
test.plot()

In [26]:
import plotly.express as px


fig = px.line(x=test.portfolio_time, y=test.portfolio)
fig.update_layout(
    xaxis_title="Время (мин.)",
    yaxis_title="Портфолио",
)
fig.show()

In [27]:
print(f"Чистая прибыль: {sum(test.trade_profits):.2f}")
pos_prof_cnt = sum([1 if prof > 0 else 0 for prof in test.trade_profits])
neg_prof_cnt = sum([1 if prof < 0 else 0 for prof in test.trade_profits])
print(f"Процент прибыльных сделок: {pos_prof_cnt / len(test.trade_profits):.2f}")
print(f"Процент убыточных сделок: {neg_prof_cnt / len(test.trade_profits):.2f}")
print(f"Самая большая прибыльная сделка: {max(test.trade_profits):.2f}")
print(f"Самая большая убыточная сделка: {min(test.trade_profits):.2f}")
print(f"Средняя прибыльная сделка: {sum([prof if prof > 0 else 0 for prof in test.trade_profits]) / pos_prof_cnt:.2f}")
print(f"Средняя убыточная сделка: {sum([prof if prof < 0 else 0 for prof in test.trade_profits]) / neg_prof_cnt:.2f}")

Чистая прибыль: -333.56
Процент прибыльных сделок: 0.29
Процент убыточных сделок: 0.71
Самая большая прибыльная сделка: 17.23
Самая большая убыточная сделка: -11.40
Средняя прибыльная сделка: 1.65
Средняя убыточная сделка: -1.38
